# Topic Modelling

In [18]:
# Import modules
# https://www.machinelearningplus.com/nlp/topic-modeling-gensim-python/
import re
import numpy as np
import pandas as pd
from pprint import pprint

# Gensim
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel

# NLTK
import nltk

# spacy for lemmatization
import spacy

# Plotting tools
import pyLDAvis
import pyLDAvis.gensim  # don't skip this
import matplotlib.pyplot as plt
%matplotlib inline

# Enable logging for gensim - optional
import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.ERROR)

import warnings
warnings.filterwarnings("ignore",category=DeprecationWarning)

In [29]:
with open("Locke_HumanUnderstandingCLEAN.txt", "r", encoding="utf-8") as file:
    Locke = file.read()

with open("Berkeley_HumanKnowledgeCLEAN.txt", "r", encoding="utf-8") as file:
    Berkeley = file.read()
    
with open("Hume_HumanUnderstandingCLEAN.txt", "r", encoding="utf-8") as file:
    Hume = file.read()
    
corpus = [Locke, Berkeley, Hume]

In [30]:
# NLTK Stop words
from nltk.corpus import stopwords
stop_words = stopwords.words('english')
stop_words.extend(['ibid'])

In [31]:
def sent_to_words(sentences):
    for sentence in sentences:
        yield(gensim.utils.simple_preprocess(str(sentence), deacc=True))  # deacc=True removes punctuations

data_words = list(sent_to_words(corpus))

print(data_words[:1])

[['an', 'essay', 'concerning', 'human', 'understanding', 'by', 'john', 'locke', 'contents', 'an', 'essay', 'concerning', 'human', 'understanding', 'epistle', 'to', 'the', 'reader', 'neither', 'principles', 'nor', 'ideas', 'are', 'innate', 'no', 'innate', 'speculative', 'principles', 'no', 'innate', 'practical', 'principles', 'other', 'considerations', 'concerning', 'innate', 'principles', 'both', 'speculative', 'and', 'practical', 'of', 'ideas', 'of', 'ideas', 'in', 'general', 'and', 'their', 'original', 'of', 'simple', 'ideas', 'of', 'simple', 'ideas', 'of', 'sense', 'idea', 'of', 'solidity', 'of', 'simple', 'ideas', 'of', 'divers', 'senses', 'of', 'simple', 'ideas', 'of', 'reflection', 'ii', 'of', 'simple', 'ideas', 'of', 'both', 'sensation', 'and', 'reflection', 'iii', 'some', 'further', 'considerations', 'concerning', 'our', 'simple', 'ideas', 'of', 'sensation', 'of', 'perception', 'of', 'retention', 'of', 'discerning', 'and', 'other', 'operations', 'of', 'the', 'mind', 'of', 'comp

In [32]:
# Build the bigram and trigram models
#bigram = gensim.models.Phrases(data_words, min_count=5, threshold=100) # higher threshold fewer phrases.
#trigram = gensim.models.Phrases(bigram[data_words], threshold=100)  

# Faster way to get a sentence clubbed as a trigram/bigram
bigram_mod = gensim.models.phrases.Phraser(bigram)
trigram_mod = gensim.models.phrases.Phraser(trigram)

# See trigram example
print(trigram_mod[bigram_mod[data_words[0]]])

['an', 'essay', 'concerning', 'human', 'understanding', 'by', 'john', 'locke', 'contents', 'an', 'essay', 'concerning', 'human', 'understanding', 'epistle', 'to', 'the', 'reader', 'neither', 'principles', 'nor', 'ideas', 'are', 'innate', 'no', 'innate', 'speculative', 'principles', 'no', 'innate', 'practical', 'principles', 'other', 'considerations', 'concerning', 'innate', 'principles', 'both', 'speculative', 'and', 'practical', 'of', 'ideas', 'of', 'ideas', 'in', 'general', 'and', 'their', 'original', 'of', 'simple', 'ideas', 'of', 'simple', 'ideas', 'of', 'sense', 'idea', 'of', 'solidity', 'of', 'simple', 'ideas', 'of', 'divers', 'senses', 'of', 'simple', 'ideas', 'of', 'reflection', 'ii', 'of', 'simple', 'ideas', 'of', 'both', 'sensation', 'and', 'reflection', 'iii', 'some', 'further', 'considerations', 'concerning', 'our', 'simple', 'ideas', 'of', 'sensation', 'of', 'perception', 'of', 'retention', 'of', 'discerning', 'and', 'other', 'operations', 'of', 'the', 'mind', 'of', 'compl

In [33]:
# Define functions for stopwords, bigrams, trigrams and lemmatization
def remove_stopwords(texts):
    return [[word for word in simple_preprocess(str(doc)) if word not in stop_words] for doc in texts]

def make_bigrams(texts):
    return [bigram_mod[doc] for doc in texts]

def make_trigrams(texts):
    return [trigram_mod[bigram_mod[doc]] for doc in texts]

def lemmatization(texts, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV']):
    """https://spacy.io/api/annotation"""
    texts_out = []
    for sent in texts:
        doc = nlp(" ".join(sent)) 
        texts_out.append([token.lemma_ for token in doc if token.pos_ in allowed_postags])
    return texts_out

In [34]:
# Remove Stop Words
data_words_nostops = remove_stopwords(data_words)

# Form Bigrams
data_words_bigrams = make_bigrams(data_words_nostops)

# Initialize spacy 'en' model, keeping only tagger component (for efficiency)
# python3 -m spacy download en
nlp = spacy.load('en', disable=['parser', 'ner'])

# Do lemmatization keeping only noun, adj, vb, adv
data_lemmatized = lemmatization(data_words_bigrams, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV'])

print(data_lemmatized[:5])

[['essay', 'concern', 'human', 'understanding', 'john', 'locke', 'content', 'essay', 'concern', 'human', 'understanding', 'epistle', 'reader', 'principle', 'idea', 'innate', 'innate', 'speculative', 'principle', 'innate', 'practical', 'principle', 'consideration', 'concern', 'innate', 'principle', 'speculative', 'practical', 'idea', 'idea', 'general', 'original', 'simple', 'idea', 'simple', 'idea', 'sense', 'idea', 'solidity', 'simple', 'idea', 'diver', 'sense', 'simple', 'idea', 'reflection', 'simple', 'idea', 'sensation', 'reflection', 'iii', 'consideration', 'concern', 'simple', 'idea', 'sensation', 'perception', 'retention', 'discern', 'operation', 'mind', 'complex', 'idea', 'complex', 'idea', 'simple', 'modesand', 'first', 'simple', 'mode', 'idea', 'space', 'idea', 'duration', 'simple', 'mode', 'idea', 'duration', 'expansion', 'consider', 'together', 'idea', 'number', 'infinity', 'simple', 'mode', 'mode', 'think', 'mode', 'pleasure', 'pain', 'power', 'mixed', 'mode', 'complex', 'i

In [35]:
# Create Dictionary
id2word = corpora.Dictionary(data_lemmatized)

# Create Corpus
texts = data_lemmatized

# Term Document Frequency
corpus = [id2word.doc2bow(text) for text in texts]

# View
print(corpus[:5])

[[(0, 1), (1, 1), (2, 2), (3, 1), (4, 2), (5, 4), (6, 23), (7, 152), (8, 1), (9, 1), (10, 1), (11, 4), (12, 2), (13, 1), (14, 2), (15, 4), (16, 9), (17, 26), (18, 33), (19, 14), (20, 12), (21, 1), (22, 188), (23, 1), (24, 8), (25, 7), (26, 1), (27, 5), (28, 1), (29, 19), (30, 36), (31, 1), (32, 5), (33, 3), (34, 29), (35, 5), (36, 1), (37, 1), (38, 3), (39, 8), (40, 12), (41, 10), (42, 8), (43, 1), (44, 4), (45, 28), (46, 1), (47, 1), (48, 104), (49, 7), (50, 58), (51, 4), (52, 7), (53, 4), (54, 2), (55, 15), (56, 11), (57, 1), (58, 34), (59, 2), (60, 29), (61, 18), (62, 5), (63, 22), (64, 1), (65, 1), (66, 94), (67, 8), (68, 392), (69, 42), (70, 2), (71, 1), (72, 1), (73, 45), (74, 58), (75, 1), (76, 1), (77, 12), (78, 1), (79, 6), (80, 1), (81, 1), (82, 8), (83, 2), (84, 16), (85, 2), (86, 1), (87, 9), (88, 105), (89, 2), (90, 1), (91, 1), (92, 1), (93, 44), (94, 1), (95, 1), (96, 3), (97, 1), (98, 42), (99, 9), (100, 1), (101, 1), (102, 1), (103, 1), (104, 1), (105, 2), (106, 2), (1

In [36]:
# Build LDA model
lda_model = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=20, 
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=10,
                                           alpha='auto',
                                           per_word_topics=True)

In [37]:
# Print the Keyword in the 10 topics
pprint(lda_model.print_topics())
doc_lda = lda_model[corpus]

[(0,
  '0.005*"idea" + 0.003*"man" + 0.003*"make" + 0.002*"think" + 0.002*"mind" + '
  '0.002*"may" + 0.002*"thing" + 0.002*"find" + 0.001*"part" + 0.001*"body"'),
 (1,
  '0.013*"may" + 0.009*"idea" + 0.008*"object" + 0.008*"nature" + '
  '0.008*"effect" + 0.007*"must" + 0.007*"experience" + 0.006*"mind" + '
  '0.006*"man" + 0.006*"reason"'),
 (2,
  '0.006*"idea" + 0.003*"mind" + 0.002*"thing" + 0.002*"man" + 0.002*"make" + '
  '0.002*"may" + 0.002*"think" + 0.002*"know" + 0.001*"knowledge" + '
  '0.001*"body"'),
 (3,
  '0.004*"idea" + 0.003*"may" + 0.002*"man" + 0.002*"mind" + 0.002*"make" + '
  '0.002*"think" + 0.001*"must" + 0.001*"thing" + 0.001*"knowledge" + '
  '0.001*"object"'),
 (4,
  '0.001*"idea" + 0.001*"man" + 0.001*"mind" + 0.001*"may" + 0.001*"make" + '
  '0.001*"thing" + 0.001*"think" + 0.001*"name" + 0.001*"truth" + '
  '0.001*"part"'),
 (5,
  '0.003*"idea" + 0.002*"man" + 0.002*"may" + 0.001*"mind" + 0.001*"think" + '
  '0.001*"make" + 0.001*"thing" + 0.001*"know" + 0.

In [38]:
# Compute Perplexity
print('\nPerplexity: ', lda_model.log_perplexity(corpus))  # a measure of how good the model is. lower the better.

# Compute Coherence Score
coherence_model_lda = CoherenceModel(model=lda_model, texts=data_lemmatized, dictionary=id2word, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)


Perplexity:  -7.152836802891361

Coherence Score:  0.25860614131209786


In [39]:
# Visualize the topics
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim.prepare(lda_model, corpus, id2word)
vis

PreparedData(topic_coordinates=            Freq  cluster  topics         x         y
topic                                                
10     75.627831        1       1  0.216209 -0.050240
1      14.732376        1       2  0.212395  0.120601
19      9.639261        1       3  0.256643 -0.053406
6       0.000033        1       4 -0.037908 -0.005384
14      0.000033        1       5 -0.032688 -0.007700
18      0.000033        1       6 -0.032543 -0.005254
0       0.000033        1       7 -0.020229 -0.013488
2       0.000033        1       8 -0.017903 -0.012637
8       0.000033        1       9 -0.049884 -0.001814
17      0.000033        1      10 -0.041452  0.012208
12      0.000033        1      11 -0.034101 -0.004869
16      0.000033        1      12  0.019145 -0.017471
15      0.000033        1      13 -0.046378 -0.007611
3       0.000032        1      14 -0.012367  0.024491
9       0.000030        1      15 -0.051285  0.001102
4       0.000029        1      16 -0.081977  0.006311
11      0.000029        1      17 -0.087215  0.007762
13      0.000029        1      18 -0.056392  0.001524
7       0.000029        1      19 -0.052698  0.003506
5       0.000029        1      20 -0.049370  0.002369, topic_info=     Category         Freq         Term        Total  loglift  logprob
term                                                                  
2741  Default  4644.000000         idea  4644.000000  30.0000  30.0000
3497  Default  2029.000000          man  2029.000000  29.0000  29.0000
3486  Default  1761.000000         make  1761.000000  28.0000  28.0000
3634  Default  1709.000000         mind  1709.000000  27.0000  27.0000
3552  Default  1585.000000          may  1585.000000  26.0000  26.0000
5808  Default  1441.000000        thing  1441.000000  25.0000  25.0000
5811  Default  1230.000000        think  1230.000000  24.0000  24.0000
3786  Default  1060.000000         name  1060.000000  23.0000  23.0000
3261  Default   942.000000    knowledge   942.000000  22.0000  22.0000
3255  Default   999.000000         know   999.000000  21.0000  21.0000
621   Default   967.000000         body   967.000000  20.0000  20.0000
4155  Default   939.000000         part   939.000000  19.0000  19.0000
6499  Default   856.000000         word   856.000000  18.0000  18.0000
6179  Default   800.000000          use   800.000000  17.0000  17.0000
6520  Default   771.000000        would   771.000000  16.0000  16.0000
2518  Default   778.000000        great   778.000000  15.0000  15.0000
2228  Default   747.000000         find   747.000000  14.0000  14.0000
4757  Default   803.000000       reason   803.000000  13.0000  13.0000
5295  Default   562.000000       simple   562.000000  12.0000  12.0000
5950  Default   623.000000        truth   623.000000  11.0000  11.0000
4409  Default   678.000000        power   678.000000  10.0000  10.0000
5563  Default   604.000000    substance   604.000000   9.0000   9.0000
5059  Default   723.000000          say   723.000000   8.0000   8.0000
3902  Default   620.000000          not   620.000000   7.0000   7.0000
5706  Default   590.000000         take   590.000000   6.0000   6.0000
738   Default   606.000000          can   606.000000   5.0000   5.0000
4601  Default   509.000000  proposition   509.000000   4.0000   4.0000
1035  Default   449.000000      complex   449.000000   3.0000   3.0000
3775  Default   637.000000         must   637.000000   2.0000   2.0000
3738  Default   615.000000       motion   615.000000   1.0000   1.0000
...       ...          ...          ...          ...      ...      ...
3497  Topic20     0.000078          man  2029.448975  -2.0324  -6.3794
3634  Topic20     0.000066         mind  1709.234985  -2.0345  -6.5532
5811  Topic20     0.000051        think  1230.469360  -1.9504  -6.7978
3255  Topic20     0.000043         know   999.206909  -1.9298  -6.9854
3486  Topic20     0.000051         make  1761.400269  -2.3249  -6.8136
5808  Topic20     0.000045        thing  1441.112671  -2.2519  -6.9413
